In [84]:
import pandas as pd
import json
import os
import numpy as np
import pickle
import datetime
import copy

In [588]:
with open('/Volumes/commons/PP-PROLOG/VENDOR_MANAGEMENT/Data_Analytics/Data_Files/Procurement_Data/Sourcing_Pipeline/Rays Trello Board.json', 'r') as f:
    trello_json = json.load(f)

In [589]:
trello_json

{'id': '5935fd150f9fbbdbc0f0320e',
 'name': 'SOURCING LIST',
 'desc': '',
 'descData': None,
 'closed': False,
 'dateClosed': None,
 'idOrganization': '593936c0054dafe3923f36d1',
 'idEnterprise': None,
 'limits': {'attachments': {'perBoard': {'status': 'ok',
    'disableAt': 36000,
    'warnAt': 28800},
   'perCard': {'status': 'ok', 'disableAt': 1000, 'warnAt': 800}},
  'boards': {'totalMembersPerBoard': {'status': 'ok',
    'disableAt': 1600,
    'warnAt': 1280},
   'totalAccessRequestsPerBoard': {'status': 'ok',
    'disableAt': 4000,
    'warnAt': 3200}},
  'cards': {'openPerBoard': {'status': 'ok',
    'disableAt': 5000,
    'warnAt': 4000},
   'openPerList': {'status': 'ok', 'disableAt': 5000, 'warnAt': 4000},
   'totalPerBoard': {'status': 'ok', 'disableAt': 2000000, 'warnAt': 1600000},
   'totalPerList': {'status': 'ok', 'disableAt': 1000000, 'warnAt': 800000}},
  'checklists': {'perBoard': {'status': 'ok',
    'disableAt': 1800000,
    'warnAt': 1440000},
   'perCard': {'statu

TODO: 
- Get member name from member ID
- Go through all cards and process them into a concrete dictionary 
- Get list name from list ID 
- Parse label name from label object (easy)

In [109]:
def get_card_labels(card):
    # Card object 
    label_list = []
    
    labels = card['labels']
    
    for label in labels:
        label_list.append(label['name'])
    
    return label_list

In [590]:
len(trello_json['cards'])

658

In [591]:
test_data.loc[test_data['TRLO - Project ID'] == '5b8546f7f3aef66064bad3d0']

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
16                  8/30/2018       EWELSH  5b8546f7f3aef66064bad3d0   

         TRLO - Project Title TRLO - Assigned To TRLO - Procurement Stage  \
16  Intercept Survey Provider         Eric Welsh        MAINTAIN CONTRACT   

   TRLO - Procurement Status TRLO - Closed Project  \
16                  Contract                  Open   

                                   TRLO - Url (Cards)  \
16  https://trello.com/c/ncEwn4FV/305-intercept-su...   

   TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
16                  12/11/2018             NaN                NaN   

   TRLO - Level of Effort TRLO - Proj In FMIS TRLO - Safety Related  \
16                    NaN                 NaN                   NaN   

   TRLO - DEI Related TRLO - SDT Review TRLO - Spend Threshold  
16                NaN               NaN                    NaN

In [592]:
trello_json['cards'][622]

{'id': '5ae33d3d6ff96aaf343091d6',
 'address': None,
 'badges': {'attachmentsByType': {'trello': {'board': 0, 'card': 0}},
  'location': False,
  'votes': 0,
  'viewingMemberVoted': False,
  'subscribed': False,
  'fogbugz': '',
  'checkItems': 0,
  'checkItemsChecked': 0,
  'checkItemsEarliestDue': None,
  'comments': 0,
  'attachments': 0,
  'description': True,
  'due': None,
  'dueComplete': False,
  'start': None},
 'checkItemStates': None,
 'closed': False,
 'coordinates': None,
 'creationMethod': None,
 'dueComplete': False,
 'dateLastActivity': '2022-01-31T16:35:55.201Z',
 'desc': 'The MBTA is seeking payment technology consulting services (the “Payments Technology Consultant”) to support the technical aspects of the implementation of the System as related to the card and mobile acceptance, payments processing and security aspects of the system',
 'descData': {'emoji': {}},
 'due': None,
 'dueReminder': None,
 'email': 'chenghanyue+2xr9z8o8dffionihfjf+2q6b48t8pdok7c8ogk6+0nwu1g

In [593]:
members = trello_json['members']
lists = trello_json['lists']

members_dict = {}
lists_dict = {}

# rename keys so that it is easier to access
for i in range(len(members)):
    members_dict[members[i]['id']] = members[i] 

for i in range(len(lists)):
    lists_dict[lists[i]['id']] = lists[i]

#print(members.keys)
#print(lists.keys)

In [318]:
lists_dict

{'5935ff7929e4fc2b7c39faeb': {'id': '5935ff7929e4fc2b7c39faeb',
  'name': 'UNKNOWN',
  'closed': True,
  'idBoard': '5935fd150f9fbbdbc0f0320e',
  'pos': 32767.75,
  'subscribed': False,
  'softLimit': None,
  'limits': {'cards': {'openPerList': {'status': 'ok',
     'disableAt': 5000,
     'warnAt': 4000},
    'totalPerList': {'status': 'ok', 'disableAt': 1000000, 'warnAt': 800000}}},
  'creationMethod': None},
 '5935fd4d15f59251a1a678b0': {'id': '5935fd4d15f59251a1a678b0',
  'name': 'MAINTAIN CONTRACT',
  'closed': True,
  'idBoard': '5935fd150f9fbbdbc0f0320e',
  'pos': 114687.125,
  'subscribed': False,
  'softLimit': None,
  'limits': {'cards': {'openPerList': {'status': 'ok',
     'disableAt': 5000,
     'warnAt': 4000},
    'totalPerList': {'status': 'ok', 'disableAt': 1000000, 'warnAt': 800000}}},
  'creationMethod': None},
 '5d7a5481c818437c522ed6c9': {'id': '5d7a5481c818437c522ed6c9',
  'name': 'SPECIFICATION HOLD',
  'closed': False,
  'idBoard': '5935fd150f9fbbdbc0f0320e',
  

In [594]:
def get_list_by_id(listID):
    return lists_dict[listID]['name']
    
def get_members_by_ids(member_ids):
    member_list = []
    
    correct_members_dict = {
        '5932cdf4d9946250ed83d611': 'Nick Easley',
        '593814b1ffff50d61a6ffefe': 'Tracey Dionne',
        '5938514c586d6db6eb1192a0': 'Joe Flynn',
        '5b0d7bd52cfb836ed06e2ce9': 'Ray Wise',
        '5b44af42f3ef6c258e7e8351': 'Eric Welsh',
        '5b7c3f05d0cca32135661211': 'Rob Weiner',
        '5bc74b04a9932625bd29bde7': 'John DeLalla',
        '5c1153ead418da18936b8c54': 'Jimmy Moynihan',
        '5c11839181a2ee0bf9cf4608': 'Kiana Hall',
        '5dadb5d0e3f9797ccc768e91': 'Iya Kazekevich',
        '5dcd7c49dab6682f4d3b9684': 'Arlyn Zuniga',
        '5fb55f187751218a60a048d7': 'Michael Pillemer'
    }
    
    if len(member_ids) == 0:
        member_list.append('Unassigned')
    elif len(member_ids) == 1:
        member_list.append(correct_members_dict[member_ids[0]])
    else:
        for member_id in member_ids:
            member_list.append(correct_members_dict[member_id])

    return member_list

def format_activity(activity_date):
    # Get Datetime object
    # 2022-01-31T16:32:29.984Z
    # Desired format:
    # DD-[Month name]-YY
    activity_date = activity_date[:len(activity_date) - 5]
    activity_datetime = datetime.datetime.strptime(activity_date, '%Y-%m-%dT%H:%M:%S')
    
    return activity_datetime.strftime('%-m/%-d/%Y')

def format_due_date(due_date):
    # Get Datetime object
    # 2022-01-31T16:32:29.984Z
    # Desired format:
    # DD-[Month name]-YY
    due_date = due_date[:len(due_date) - 5]
    due_datetime = datetime.datetime.strptime(due_date, '%Y-%m-%dT%H:%M:%S')
    
    return due_datetime.strftime('%-m/%-d/%Y')
    
def format_archival(archived_status):
    if archived_status:
        return 'Yes'
    else:
        return 'No'
    
def format_closed(closed_status):
    if closed_status:
        return 'Closed'
    else:
        return 'Open'

def get_status_by_list(list_id):
    procurement_status_dict = {
        '5935fd2a32d6de7c51454b64' :  'Pipeline',
        '5bc9db91fb62c1685a51d7ef' :  'Pipeline',
        '5935fd3423c4cedaedf011ab' :  'Solicitation',
        '593d3e265758fdb44be5a8fb' :  'Solicitation',
        '5935fd3b01374ff1af03c73c' :  'Solicitation',
        '5935fd418c23c980874a7998' :  'Solicitation',
        '5b3b83aa1bbe3f205aba9997' :  'Solicitation',
        '5935fd4566bf9d5a68e1f8d3' :  'Contract',
        '5935fd4d15f59251a1a678b0' :  'Contract',
        '5937dbb9fbf481f047aa4198' :  'Contract',
        '5937db640d1123a81cf03bd3' :  'Closed',
        '5cac95843ce3f744def010b2' :  'Closed',
        '593a94f408ed531f8b4019ba' :  'On Hold',
        '593a94f605f7adbfabad8162' :  'On Hold',
        '59807ef4e05533b498c69f10' :  'On Hold',
        '5d7a5481c818437c522ed6c9' :  'On Hold'}
    
    # Translate list ID to procurement status
    
    return procurement_status_dict[list_id]

def get_stage_by_list(list_id):
    procuremnent_stage_dict = {
        '5935fd2a32d6de7c51454b64' : 'PIPELINE',
        '5935fd3423c4cedaedf011ab' : '1. PREPARE RFP',
        '5935fd3b01374ff1af03c73c' : '2. SOURCING ACTIVITIES',
        '5935fd418c23c980874a7998' : '3. EVALUATE RESPONSE',
        '5935fd4566bf9d5a68e1f8d3' : '4. FINALIZE CONTRACT',
        '5935fd4d15f59251a1a678b0' : 'MAINTAIN CONTRACT (Archived)',
        '5937db640d1123a81cf03bd3' : 'COMPLETE FOR THE WEEK',
        '5937dbb9fbf481f047aa4198' : 'MAINTAIN CONTRACT',
        '593a94f408ed531f8b4019ba' : 'FOR CPO REVIEW',
        '593a94f605f7adbfabad8162' : '** LEGAL ISSUE **',
        '593d3e265758fdb44be5a8fb' : '1. PREPARE RFP (Archived)',
        '59807ef4e05533b498c69f10' : '** INSURANCE DELAY **',
        '5b3b83aa1bbe3f205aba9997' : 'LIVE VEHICLE PROCUREMENTS',
        '5bc9db91fb62c1685a51d7ef' : 'PIPELINE (Archived)',
        '5cac95843ce3f744def010b2' : 'CANCELLED INITIATIVES',
        '5d7a5481c818437c522ed6c9' : 'SPECIFICATION HOLD',
        '5f0489b9c31675327f2c7558' : 'VEH PROC IN WARRANTY'
    }
    
    return procuremnent_stage_dict[list_id]

In [595]:
format_activity('2022-01-31T16:32:29.984Z')

'1/31/2022'

In [596]:
card_list = []
id_set = set()

for card in trello_json['cards']:
    id_set.add(card['id'])
    
    labels = get_card_labels(card)
    
    procurement_step = get_stage_by_list(card['idList'])
    members = get_members_by_ids(card['idMembers'])
    
    last_updated = format_activity(card['dateLastActivity'])
    archived = format_archival(card['closed'])
    closed = format_closed(card['closed'])
    
    if card['due'] is not None:
        due_date = format_due_date(card['due'])
    else:
        due_date = np.nan
    
    status = get_status_by_list(card['idList'])
    
    if len(labels) == 0:
        labels = ['']
        
    for label in labels:
        if len(members) > 1:
            for member in members:
                card_dict = {'Procurement Stage': procurement_step, 
                    'Project Title': card['name'],
                    'Label Name': label,
                    'Due Date': due_date, 
                    'Last Updated': last_updated, 
                    'Project ID': card['id'], 
                    'Assigned To': member,
                    'Closed Project': closed, 
                    'Procurement Status': status, 
                    'Url (Cards)': card['url'], 
                    'Archived': archived}

                card_list.append(card_dict)

        else:
            card_dict = {'Procurement Stage': procurement_step, 
                        'Project Title': card['name'],
                        'Label Name': label,
                        'Due Date': due_date, 
                        'Last Updated': last_updated, 
                        'Project ID': card['id'], 
                        'Assigned To': members[0],
                        'Closed Project': closed, 
                        'Procurement Status': status, 
                        'Url (Cards)': card['url'], 
                        'Archived': archived}

            card_list.append(card_dict)

In [597]:
full_trello_df = pd.DataFrame(card_list)

In [598]:
full_trello_df

Procurement Stage  \
0     MAINTAIN CONTRACT (Archived)   
1     MAINTAIN CONTRACT (Archived)   
2     MAINTAIN CONTRACT (Archived)   
3     MAINTAIN CONTRACT (Archived)   
4     MAINTAIN CONTRACT (Archived)   
...                            ...   
1027         CANCELLED INITIATIVES   
1028         CANCELLED INITIATIVES   
1029         CANCELLED INITIATIVES   
1030                FOR CPO REVIEW   
1031                FOR CPO REVIEW   

                                          Project Title          Label Name  \
0                                        Printers XEROX         high effort   
1                  RFR-3-17 BLANKET CONSULTING SERVICES                       
2                              325 NEW BUSSES-NEW FLYER                       
3           MIDLIFE OVERHAUL-192 NEOPLAN BUSSES-MIDWEST                       
4     Midlife Overhaul of 74 Bi-Level Commuter Rail ...                       
...                                                 ...                 ...   
1027                      Dock & Dockless Bikes Program                       
1028              RFP 27F-20 Travel Instruction Program  no requisition yet   
1029                         Traction Power Submetering       medium effort   
1030                    BIRD CONTROL SERVICES--$310,000                       
1031                      CLEANING CONTRACT AMMENDMENTS                       

       Due Date Last Updated                Project ID    Assigned To  \
0           NaN    6/11/2017  5936005258e843c083369f7a     Unassigned   
1           NaN    6/11/2017  5935ff8a24be6b67e34c664a     Unassigned   
2           NaN     4/6/2018  5935fff68c18dab27b4a2433     Unassigned   
3           NaN     4/6/2018  59360024def2da683e72eea7     Unassigned   
4           NaN    8/16/2019  593967d28eede32c6acfa1d7      Joe Flynn   
...         ...          ...                       ...            ...   
1027   3/1/2019    7/14/2020  5b71fe2037ef867c9f0d818f       Ray Wise   
1028        NaN    9/22/2020  5d9c8e9bee52b40e3447c8eb  Tracey Dionne   
1029  5/22/2019     6/2/2020  5c38c9cfcdcd5f4e2ef5bcb3   John DeLalla   
1030        NaN    6/14/2017  5935fec09bca98d1bc78aebc  Tracey Dionne   
1031        NaN     3/5/2018  5937dbb9fbf481f047aa41af      Joe Flynn   

     Closed Project Procurement Status  \
0            Closed           Contract   
1            Closed           Contract   
2            Closed           Contract   
3            Closed           Contract   
4            Closed           Contract   
...             ...                ...   
1027         Closed             Closed   
1028         Closed             Closed   
1029         Closed             Closed   
1030         Closed            On Hold   
1031         Closed            On Hold   

                                            Url (Cards) Archived  
0       https://trello.com/c/7Af78i02/69-printers-xerox      Yes  
1     https://trello.com/c/0W3eHbJB/49-rfr-3-17-blan...      Yes  
2     https://trello.com/c/33WtO0zs/58-325-new-busse...      Yes  
3     https://trello.com/c/Yd3hJqOF/62-midlife-overh...      Yes  
4     https://trello.com/c/5lC9s3Gr/119-midlife-over...      Yes  
...                                                 ...      ...  
1027  https://trello.com/c/ItjmOgCV/295-dock-dockles...      Yes  
1028  https://trello.com/c/hnFU5IQ7/516-rfp-27f-20-t...      Yes  
1029  https://trello.com/c/8IRWW8vM/405-traction-pow...      Yes  
1030  https://trello.com/c/12OqdIn1/34-bird-control-...      Yes  
1031  https://trello.com/c/t0oBsUMh/89-cleaning-cont...      Yes  

[1032 rows x 11 columns]

In [599]:
full_trello_df.loc[full_trello_df['Project ID'] == '5cf94cb53c10b4869974287f']

Procurement Stage                   Project Title          Label Name  \
20  SPECIFICATION HOLD  Peak Service Expansion Service         high effort   
21  SPECIFICATION HOLD  Peak Service Expansion Service  no requisition yet   

   Due Date Last Updated                Project ID Assigned To Closed Project  \
20      NaN    4/28/2020  5cf94cb53c10b4869974287f  Kiana Hall         Closed   
21      NaN    4/28/2020  5cf94cb53c10b4869974287f  Kiana Hall         Closed   

   Procurement Status                                        Url (Cards)  \
20            On Hold  https://trello.com/c/Vhs086Cv/465-peak-service...   
21            On Hold  https://trello.com/c/Vhs086Cv/465-peak-service...   

   Archived  
20      Yes  
21      Yes

Aggregate steps

- Project ID (key field)
- Extracting Labels from these
- Aggregate to One Project ID per row for the main dataframe
- Separate dataframe of Project ID: Label

Missing ~200 unique project ID's (NOT ANYMORE)

In [600]:
for l in lists_dict:
    print(lists_dict[l]['name'])

UNKNOWN
MAINTAIN CONTRACT
SPECIFICATION HOLD
RFI
PIPELINE
PIPELINE
1. PREPARE RFP
1. PREPARE RFP
2a. BID OPEN
2. SOURCING ACTIVITIES
COVID-19 Hold
2b. BID EVALUATION
Risk Management Review 1.5
** INSURANCE DELAY **
3. EVALUATE RESPONSE
4. FINALIZE CONTRACT
LIVE VEHICLE PROCUREMENTS
VEHICLE PROCUREMENTS IN WARRANTY
MAINTAIN CONTRACT
1A. CONSTRUCTION BID ON HOLD
CONSTRUCTION PAUSED
FOR CPO REVIEW


In [601]:
print(sorted(test_data['TRLO - Procurement Status'].unique()))
print(sorted(test_data['TRLO - Procurement Stage'].unique()))
print(sorted(full_trello_df['Procurement Status'].unique()))
print(sorted(full_trello_df['Procurement Stage'].unique()))

['Closed', 'Contract', 'On Hold', 'Pipeline', 'Solicitation']
['** INSURANCE DELAY **', '** LEGAL ISSUE **', '1. PREPARE RFP', '1. PREPARE RFP (Archived)', '2. SOURCING ACTIVITIES', '3. EVALUATE RESPONSE', '4. FINALIZE CONTRACT', 'CANCELLED INITIATIVES', 'COMPLETE FOR THE WEEK', 'FOR CPO REVIEW', 'LIVE VEHICLE PROCUREMENTS', 'MAINTAIN CONTRACT', 'MAINTAIN CONTRACT (Archived)', 'PIPELINE', 'PIPELINE (Archived)', 'SPECIFICATION HOLD']
['Closed', 'Contract', 'On Hold', 'Pipeline', 'Solicitation']
['** INSURANCE DELAY **', '** LEGAL ISSUE **', '1. PREPARE RFP', '1. PREPARE RFP (Archived)', '2. SOURCING ACTIVITIES', '3. EVALUATE RESPONSE', '4. FINALIZE CONTRACT', 'CANCELLED INITIATIVES', 'COMPLETE FOR THE WEEK', 'FOR CPO REVIEW', 'LIVE VEHICLE PROCUREMENTS', 'MAINTAIN CONTRACT', 'MAINTAIN CONTRACT (Archived)', 'PIPELINE', 'PIPELINE (Archived)', 'SPECIFICATION HOLD']


**TODO:**
- change last updated format to %-m/%-d/%Y (DONE)
- change Procurement Stage (from alias) (DONE)
- refine Procurement Status (from alias from david) (DONE)
- change default due date  to nan (DONE)

In [604]:
print(len(recent_test_data['TRLO -  Project ID'].unique()))
print(len(full_trello_df['Project ID'].unique()))

658
658


In [605]:
project_id_dict = {}

for project_id in list(full_trello_df['Project ID'].unique()):
    filtered_df = full_trello_df.loc[full_trello_df['Project ID'] == project_id]
    
    project_id_dict[project_id] = list(filtered_df['Label Name'])

In [606]:
project_id_dict

{'5936005258e843c083369f7a': ['high effort'],
 '5935ff8a24be6b67e34c664a': [''],
 '5935fff68c18dab27b4a2433': [''],
 '59360024def2da683e72eea7': [''],
 '593967d28eede32c6acfa1d7': [''],
 '59396dd8cd7befe1a2550a01': [''],
 '59396e0630d566a4700b3d94': [''],
 '59396e390a327b02f1974c9d': [''],
 '5e276315d246a30a3215aff0': ['federal funding', 'SAFETY', 'medium effort'],
 '5d8d3980ff61920b5bb13025': [''],
 '5d8b7a9911e9da0437489d6d': [''],
 '5d9b800ebd12082241ad2b10': ['high effort', 'no ssj yet', 'on hold'],
 '5d9e10d77fc396790f2f7736': ['medium effort', 'no ssj yet'],
 '5efb38922554154bbda1ff6e': ['low effort', 'SAFETY'],
 '5cf94cb53c10b4869974287f': ['high effort', 'no requisition yet'],
 '5c0ef4b5d7cced1295e1bcae': ['medium effort'],
 '5e42b4d01810d282fee2fa8f': ['medium effort'],
 '5d7a4ebda43f466975ef8af8': ['no requisition yet',
  'medium effort',
  'on hold'],
 '5e42b0d9e3e6064af198b19e': ['SAFETY', 'on hold', 'high effort'],
 '5e6a3db5d160ab3c4529fb41': ['high effort', 'on hold'],
 

In [341]:
test_data = pd.read_csv('trello_test_output.csv')

test_data.rename(columns={'TRLO -  Project ID': 'TRLO - Project ID'}, inplace=True)

In [342]:
test_data

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
0                   10/11/2019      AZUNIGA  5d9e5e133c89748e6d09fe50   
1                    3/28/2019       EWELSH  5c9a22187ffbcd4fdb595644   
2                    8/30/2018       EWELSH  5b85467e8df1a105def4f6e4   
3                    3/14/2019       EWELSH  5c87e5c08d21258227d5e7e0   
4                   10/21/2018       EWELSH  5bc9db92fb62c1685a51d80e   
..                         ...          ...                       ...   
659                   6/4/2021   UNASSIGNED  60b7e349d8199b64d97ed6e7   
660                  6/11/2021   UNASSIGNED  60c0ad8a8ffd1e643ca6a001   
661                  8/18/2021   UNASSIGNED  611ad49b21c5f3226604d6c9   
662                 11/26/2021   UNASSIGNED  619e7a15d5f379538aed9640   
663                   6/8/2017   UNASSIGNED  5935fd710d0ae18f54c13cb3   

                         TRLO - Project Title TRLO - Assigned To  \
0          Trapeze Transit Master Negotiation       Arlyn Zuniga   
1    Bus Amenities Request for Qualifications         Eric Welsh   
2                        Catch Basin Cleaning         Eric Welsh   
3           Temporary Staff Program RFP (SWA)         Eric Welsh   
4              RFR 142-17 - MBTA Drug Testing         Eric Welsh   
..                                        ...                ...   
659                               Budget Tool         Unassigned   
660               Printers - Newsletter, etc.         Unassigned   
661                         Pipeline Template         Unassigned   
662                                 OCC Board         Unassigned   
663                       Buy America Auditor         Unassigned   

    TRLO - Procurement Stage TRLO - Procurement Status TRLO - Closed Project  \
0       4. FINALIZE CONTRACT                  Contract                Closed   
1       3. EVALUATE RESPONSE              Solicitation                Closed   
2                   PIPELINE                  Pipeline                Closed   
3                   PIPELINE                  Pipeline                Closed   
4        PIPELINE (Archived)                  Pipeline                Closed   
..                       ...                       ...                   ...   
659                 PIPELINE                  Pipeline                  Open   
660                 PIPELINE                  Pipeline                  Open   
661                 PIPELINE                  Pipeline                  Open   
662                 PIPELINE                  Pipeline                  Open   
663       SPECIFICATION HOLD                   On Hold                  Open   

                                    TRLO - Url (Cards)  \
0    https://trello.com/c/L2CbZXqh/518-trapeze-tran...   
1    https://trello.com/c/ezPNruB1/430-bus-amenitie...   
2    https://trello.com/c/VBWa1ACB/304-catch-basin-...   
3    https://trello.com/c/xPFn0zg3/423-temporary-st...   
4    https://trello.com/c/A3eiX1mL/343-rfr-142-17-m...   
..                                                 ...   
659      https://trello.com/c/ZjzZhn2A/749-budget-tool   
660  https://trello.com/c/LA8Eh0ra/752-printers-new...   
661  https://trello.com/c/GeKbE91l/773-pipeline-tem...   
662        https://trello.com/c/gOyRXUBA/813-occ-board   
663  https://trello.com/c/avpBel1a/4-buy-america-au...   

    TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
0                     5/18/2021             NaN                NaN   
1                     11/1/2019             NaN                NaN   
2                     9/18/2018             NaN                NaN   
3                     5/28/2019             NaN                NaN   
4                    10/19/2018             NaN                NaN   
..                          ...             ...                ...   
659                   1/12/2022             NaN                NaN   
660                   10/5/2021             NaN                NaN   
661                   

In [610]:
print(test_data['TRLO - Fund Source'].unique())
print(test_data['TRLO - Level of Effort'].unique())
print(test_data['TRLO - Proj In FMIS'].unique())
print(test_data['TRLO - Safety Related'].unique())
print(test_data['TRLO - DEI Related'].unique())
print(test_data['TRLO - SDT Review'].unique())
print(test_data['TRLO - Spend Threshold'].unique())
print(test_data['TRLO - Procurement Status'].unique())

[nan 'Operations Funded' 'Capital Funded' 'Federal Funding']
['High Effort' 'Medium Effort' nan 'Low Effort']
[nan 'No Requistion Yet']
[nan 'Safety']
[nan 'Includes DEI Evaluation']
[nan 'Reviewed by SDT - Potential Candidate'
 'Reviewed by SDT - Not a Candidate'
 'Reviewed by SDT - Potential Small Biz']
[nan '>$250k Spend' '<$250k']
['Contract' 'Solicitation' 'Pipeline' 'On Hold' 'Closed']


In [611]:
label_transformation_dict = {
    'SAFETY': 'Safety',
    'INCLUDES DEI EVALUATION': 'Includes DEI Evaluation',
    'high effort': 'High Effort',
    'medium effort': 'Medium Effort',
    'low effort': 'Low Effort',
    'federal funding': 'Federal Funding',
    'no requisition yet': 'No Requistion Yet',
    'operations funded': 'Operations Funded',
    'capital funded': 'Capital Funded',
    'Review by SDT - Potential Candidate': 'Reviewed by SDT - Potential Candidate'
}

In [612]:
full_trello_df['Label Name'].unique()

array(['high effort', '', 'federal funding', 'SAFETY', 'medium effort',
       'no ssj yet', 'on hold', 'low effort', 'no requisition yet',
       'Review by SDT - Potential Candidate', '>$250k Spend', '<$250k',
       'operations funded', 'capital funded', 'INCLUDES DEI EVALUATION',
       'Reviewed by SDT - Not a Candidate',
       'Reviewed by SDT - Potential Small Business'], dtype=object)

In [613]:
fund_source_labels = ['Operations Funded', 'Capital Funded', 'Federal Funding']
effort_level_labels = ['High Effort', 'Medium Effort', 'Low Effort']
sdt_review_labels = ['Reviewed by SDT - Potential Candidate', 
                     'Reviewed by SDT - Not a Candidate', 
                     'Reviewed by SDT - Potential Small Biz']
spend_thresh_labels = ['>$250k Spend', '<$250k']

In [614]:
def construct_label_df(project_id_dict):
    # For each label, make a new row (dictionary)
    # row should contain project ID, and all label names 
    
    default_label_dict = {'TRLO - Fund Source': np.nan,
                         'TRLO - Level of Effort': np.nan,
                         'TRLO - Proj In FMIS': np.nan,
                         'TRLO - Safety Related': np.nan,
                         'TRLO - DEI Related': np.nan,
                         'TRLO - SDT Review': np.nan,
                         'TRLO - Spend Threshold': np.nan}
    
    label_row_list = []
    
    for project_id in project_id_dict:
        project_labels = project_id_dict[project_id]
        
        label_dict = copy.deepcopy(default_label_dict)
        label_dict['TRLO - Project ID'] = project_id
        
        for label in project_labels:
            if label in label_transformation_dict:
                formatted_label = label_transformation_dict[label]
            else:
                formatted_label = label
            #print(formatted_label)

            # if label is in each thing, then add it to its respective column
            if formatted_label in fund_source_labels:
                label_dict['TRLO - Fund Source'] = formatted_label

            elif formatted_label in effort_level_labels:
                label_dict['TRLO - Level of Effort'] = formatted_label

            elif formatted_label in sdt_review_labels:
                label_dict['TRLO - SDT Review'] = formatted_label

            elif formatted_label in spend_thresh_labels:
                #print(formatted_label)
                label_dict['TRLO - Spend Threshold'] = formatted_label

            elif formatted_label == 'Safety':
                #print('Safety')
                label_dict['TRLO - Safety Related'] = formatted_label
            elif formatted_label == 'Includes DEI Evaluation':
                #print('DEI Eval')
                label_dict['TRLO - DEI Related'] = formatted_label
            elif formatted_label == 'No Requistion Yet':
                #print('No Req')
                label_dict['TRLO - Proj In FMIS'] = formatted_label
        
        label_row_list.append(label_dict)
        
    return pd.DataFrame(label_row_list)

In [615]:
label_df = construct_label_df(project_id_dict)

In [616]:
trello_no_labels = full_trello_df.drop('Label Name', axis=1).astype('str').drop_duplicates().reset_index()
trello_no_labels

index             Procurement Stage  \
0        0  MAINTAIN CONTRACT (Archived)   
1        1  MAINTAIN CONTRACT (Archived)   
2        2  MAINTAIN CONTRACT (Archived)   
3        3  MAINTAIN CONTRACT (Archived)   
4        4  MAINTAIN CONTRACT (Archived)   
..     ...                           ...   
664   1027         CANCELLED INITIATIVES   
665   1028         CANCELLED INITIATIVES   
666   1029         CANCELLED INITIATIVES   
667   1030                FOR CPO REVIEW   
668   1031                FOR CPO REVIEW   

                                         Project Title   Due Date  \
0                                       Printers XEROX        nan   
1                 RFR-3-17 BLANKET CONSULTING SERVICES        nan   
2                             325 NEW BUSSES-NEW FLYER        nan   
3          MIDLIFE OVERHAUL-192 NEOPLAN BUSSES-MIDWEST        nan   
4    Midlife Overhaul of 74 Bi-Level Commuter Rail ...        nan   
..                                                 ...        ...   
664                      Dock & Dockless Bikes Program   3/1/2019   
665              RFP 27F-20 Travel Instruction Program        nan   
666                         Traction Power Submetering  5/22/2019   
667                    BIRD CONTROL SERVICES--$310,000        nan   
668                      CLEANING CONTRACT AMMENDMENTS        nan   

    Last Updated                Project ID    Assigned To Closed Project  \
0      6/11/2017  5936005258e843c083369f7a     Unassigned         Closed   
1      6/11/2017  5935ff8a24be6b67e34c664a     Unassigned         Closed   
2       4/6/2018  5935fff68c18dab27b4a2433     Unassigned         Closed   
3       4/6/2018  59360024def2da683e72eea7     Unassigned         Closed   
4      8/16/2019  593967d28eede32c6acfa1d7      Joe Flynn         Closed   
..           ...                       ...            ...            ...   
664    7/14/2020  5b71fe2037ef867c9f0d818f       Ray Wise         Closed   
665    9/22/2020  5d9c8e9bee52b40e3447c8eb  Tracey Dionne         Closed   
666     6/2/2020  5c38c9cfcdcd5f4e2ef5bcb3   John DeLalla         Closed   
667    6/14/2017  5935fec09bca98d1bc78aebc  Tracey Dionne         Closed   
668     3/5/2018  5937dbb9fbf481f047aa41af      Joe Flynn         Closed   

    Procurement Status                                        Url (Cards)  \
0             Contract    https://trello.com/c/7Af78i02/69-printers-xerox   
1             Contract  https://trello.com/c/0W3eHbJB/49-rfr-3-17-blan...   
2             Contract  https://trello.com/c/33WtO0zs/58-325-new-busse...   
3             Contract  https://trello.com/c/Yd3hJqOF/62-midlife-overh...   
4             Contract  https://trello.com/c/5lC9s3Gr/119-midlife-over...   
..                 ...                                                ...   
664             Closed  https://trello.com/c/ItjmOgCV/295-dock-dockles...   
665             Closed  https://trello.com/c/hnFU5IQ7/516-rfp-27f-20-t...   
666             Closed  https://trello.com/c/8IRWW8vM/405-traction-pow...   
667            On Hold  https://trello.com/c/12OqdIn1/34-bird-control-...   
668            On Hold  https://trello.com/c/t0oBsUMh/89-cleaning-cont...   

    Archived  
0        Yes  
1        Yes  
2        Yes  
3        Yes  
4        Yes  
..       ...  
664      Yes  
665      Yes  
666      Yes  
667      Yes  
668      Yes  

[669 rows x 11 columns]

In [617]:
trello_no_labels.rename(columns={'Project ID': 'TRLO - Project ID'}, inplace=True)

In [618]:
trello_with_labels = trello_no_labels.merge(label_df, on='TRLO - Project ID', how='left')
trello_with_labels.drop('index', axis=1, inplace=True)

In [619]:
trello_with_labels

Procurement Stage  \
0    MAINTAIN CONTRACT (Archived)   
1    MAINTAIN CONTRACT (Archived)   
2    MAINTAIN CONTRACT (Archived)   
3    MAINTAIN CONTRACT (Archived)   
4    MAINTAIN CONTRACT (Archived)   
..                            ...   
664         CANCELLED INITIATIVES   
665         CANCELLED INITIATIVES   
666         CANCELLED INITIATIVES   
667                FOR CPO REVIEW   
668                FOR CPO REVIEW   

                                         Project Title   Due Date  \
0                                       Printers XEROX        nan   
1                 RFR-3-17 BLANKET CONSULTING SERVICES        nan   
2                             325 NEW BUSSES-NEW FLYER        nan   
3          MIDLIFE OVERHAUL-192 NEOPLAN BUSSES-MIDWEST        nan   
4    Midlife Overhaul of 74 Bi-Level Commuter Rail ...        nan   
..                                                 ...        ...   
664                      Dock & Dockless Bikes Program   3/1/2019   
665              RFP 27F-20 Travel Instruction Program        nan   
666                         Traction Power Submetering  5/22/2019   
667                    BIRD CONTROL SERVICES--$310,000        nan   
668                      CLEANING CONTRACT AMMENDMENTS        nan   

    Last Updated         TRLO - Project ID    Assigned To Closed Project  \
0      6/11/2017  5936005258e843c083369f7a     Unassigned         Closed   
1      6/11/2017  5935ff8a24be6b67e34c664a     Unassigned         Closed   
2       4/6/2018  5935fff68c18dab27b4a2433     Unassigned         Closed   
3       4/6/2018  59360024def2da683e72eea7     Unassigned         Closed   
4      8/16/2019  593967d28eede32c6acfa1d7      Joe Flynn         Closed   
..           ...                       ...            ...            ...   
664    7/14/2020  5b71fe2037ef867c9f0d818f       Ray Wise         Closed   
665    9/22/2020  5d9c8e9bee52b40e3447c8eb  Tracey Dionne         Closed   
666     6/2/2020  5c38c9cfcdcd5f4e2ef5bcb3   John DeLalla         Closed   
667    6/14/2017  5935fec09bca98d1bc78aebc  Tracey Dionne         Closed   
668     3/5/2018  5937dbb9fbf481f047aa41af      Joe Flynn         Closed   

    Procurement Status                                        Url (Cards)  \
0             Contract    https://trello.com/c/7Af78i02/69-printers-xerox   
1             Contract  https://trello.com/c/0W3eHbJB/49-rfr-3-17-blan...   
2             Contract  https://trello.com/c/33WtO0zs/58-325-new-busse...   
3             Contract  https://trello.com/c/Yd3hJqOF/62-midlife-overh...   
4             Contract  https://trello.com/c/5lC9s3Gr/119-midlife-over...   
..                 ...                                                ...   
664             Closed  https://trello.com/c/ItjmOgCV/295-dock-dockles...   
665             Closed  https://trello.com/c/hnFU5IQ7/516-rfp-27f-20-t...   
666             Closed  https://trello.com/c/8IRWW8vM/405-traction-pow...   
667            On Hold  https://trello.com/c/12OqdIn1/34-bird-control-...   
668            On Hold  https://trello.com/c/t0oBsUMh/89-cleaning-cont...   

    Archived TRLO - Fund Source TRLO - Level of Effort TRLO - Proj In FMIS  \
0        Yes                NaN            High Effort                 NaN   
1        Yes                NaN                    NaN                 NaN   
2        Yes                NaN                    NaN                 NaN   
3        Yes                NaN                    NaN                 NaN   
4        Yes                NaN                    NaN                 NaN   
..       ...                ...                    ...                 ...   
664      Yes                NaN                    NaN                 NaN   
665      Yes                NaN                    NaN   No Requistion Yet   
666      Yes                NaN          Medium Effort                 NaN   
667      Yes                NaN                    NaN                 NaN   
668      Yes                NaN               

In [ ]:
# Pivot Labels to Columns
# Effort is different levels
# Funding is different levels
# DEI is greater or less than $250k

# End result: Each row is a project ID, has labels as column names. 

In [620]:
# Rename columns

trello_rename_key = {
    'Assigned To': 'TRLO - Assigned To',
    'Archived': 'TRLO - Archived',
    'Closed Project': 'TRLO - Closed Project',
    'Due Date': 'TRLO - Due Date',
    'Last Updated (Cards)': 'TRLO - Last Updated (Cards)',
    'Procurement Stage': 'TRLO - Procurement Stage',
    'Procurement Status': 'TRLO - Procurement Status',
    'Project ID': 'TRLO - Project ID',
    'Project Title': 'TRLO - Project Title',
    'Url (Cards)': 'TRLO - Url Cards',
}

trello_with_labels.rename(columns = trello_rename_key, inplace=True)

In [621]:
# Buyer calculations

buyer_dict = {
    'Arlyn Zuniga': 'AZUNIGA',
    'Jimmy Moynihan': 'JMOYNIHAN',
    'John DeLalla': 'JDELALLA',
    'Joe Flynn': 'AFLYNN',
    'Kiana Hall': 'KHALL',
    'Ray Wise': 'RWISE',
    'Rob Weiner': 'RWEINER',
    'Tracey Dionne': 'TDIONNE',
    'Eric Welsh': 'EWELSH',
    'Nicholas Easley': 'NEASLEY',
    'Unassigned': 'UNASSIGNED',
    'Michael Pillemer': 'MPILLEMER'
}

trello_with_labels['TRLO - Buyer'] = 'no buyer'

for buyer in buyer_dict:
    trello_with_labels.loc[trello_with_labels['TRLO - Assigned To'] == buyer, 'TRLO - Buyer'] = buyer_dict[buyer]

In [622]:
# Format date created

def get_date_hex(row):
    return row['TRLO - Project ID'][0:8].upper()

#trello_with_labels['Create Date Hex'] = trello_with_labels.apply(get_date_hex, axis=1)

#trello_with_labels['Project Timestamp Decimal'] = trello_with_labels.apply(lambda x: int(x['Create Date Hex'], 16), axis=1)

trello_with_labels['TRLO - Project Create Date'] = trello_with_labels.apply(lambda x: datetime.datetime.fromtimestamp(int(x['TRLO - Project ID'][0:8],16)).strftime('%-m/%-d/%Y'), axis=1)

#trello_with_labels.drop(['Create Date Hex', 'Project Timestamp Decimal'], axis=1, inplace=True)

In [623]:
# Reorder columns

trello_with_labels.rename(columns = {'TRLO - Url Cards': 'TRLO - Url (Cards)',
                                    'Last Updated': 'TRLO - Last Updated (Cards)',
                                    'TRLO - Proj in FMIS': 'TRLO - Proj In FMIS'}, inplace=True)

trello_with_labels_right_order = trello_with_labels[['TRLO - Project Create Date', 'TRLO - Buyer', 'TRLO - Project ID',
       'TRLO - Project Title', 'TRLO - Assigned To',
       'TRLO - Procurement Stage', 'TRLO - Procurement Status',
       'TRLO - Closed Project', 'TRLO - Url (Cards)',
       'TRLO - Last Updated (Cards)', 'TRLO - Due Date', 'TRLO - Fund Source',
       'TRLO - Level of Effort', 'TRLO - Proj In FMIS',
       'TRLO - Safety Related', 'TRLO - DEI Related', 'TRLO - SDT Review',
       'TRLO - Spend Threshold']]

In [624]:
trello_with_labels_right_order

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
0                     6/5/2017   UNASSIGNED  5936005258e843c083369f7a   
1                     6/5/2017   UNASSIGNED  5935ff8a24be6b67e34c664a   
2                     6/5/2017   UNASSIGNED  5935fff68c18dab27b4a2433   
3                     6/5/2017   UNASSIGNED  59360024def2da683e72eea7   
4                     6/8/2017       AFLYNN  593967d28eede32c6acfa1d7   
..                         ...          ...                       ...   
664                  8/13/2018        RWISE  5b71fe2037ef867c9f0d818f   
665                  10/8/2019      TDIONNE  5d9c8e9bee52b40e3447c8eb   
666                  1/11/2019     JDELALLA  5c38c9cfcdcd5f4e2ef5bcb3   
667                   6/5/2017      TDIONNE  5935fec09bca98d1bc78aebc   
668                   6/7/2017       AFLYNN  5937dbb9fbf481f047aa41af   

                                  TRLO - Project Title TRLO - Assigned To  \
0                                       Printers XEROX         Unassigned   
1                 RFR-3-17 BLANKET CONSULTING SERVICES         Unassigned   
2                             325 NEW BUSSES-NEW FLYER         Unassigned   
3          MIDLIFE OVERHAUL-192 NEOPLAN BUSSES-MIDWEST         Unassigned   
4    Midlife Overhaul of 74 Bi-Level Commuter Rail ...          Joe Flynn   
..                                                 ...                ...   
664                      Dock & Dockless Bikes Program           Ray Wise   
665              RFP 27F-20 Travel Instruction Program      Tracey Dionne   
666                         Traction Power Submetering       John DeLalla   
667                    BIRD CONTROL SERVICES--$310,000      Tracey Dionne   
668                      CLEANING CONTRACT AMMENDMENTS          Joe Flynn   

         TRLO - Procurement Stage TRLO - Procurement Status  \
0    MAINTAIN CONTRACT (Archived)                  Contract   
1    MAINTAIN CONTRACT (Archived)                  Contract   
2    MAINTAIN CONTRACT (Archived)                  Contract   
3    MAINTAIN CONTRACT (Archived)                  Contract   
4    MAINTAIN CONTRACT (Archived)                  Contract   
..                            ...                       ...   
664         CANCELLED INITIATIVES                    Closed   
665         CANCELLED INITIATIVES                    Closed   
666         CANCELLED INITIATIVES                    Closed   
667                FOR CPO REVIEW                   On Hold   
668                FOR CPO REVIEW                   On Hold   

    TRLO - Closed Project                                 TRLO - Url (Cards)  \
0                  Closed    https://trello.com/c/7Af78i02/69-printers-xerox   
1                  Closed  https://trello.com/c/0W3eHbJB/49-rfr-3-17-blan...   
2                  Closed  https://trello.com/c/33WtO0zs/58-325-new-busse...   
3                  Closed  https://trello.com/c/Yd3hJqOF/62-midlife-overh...   
4                  Closed  https://trello.com/c/5lC9s3Gr/119-midlife-over...   
..                    ...                                                ...   
664                Closed  https://trello.com/c/ItjmOgCV/295-dock-dockles...   
665                Closed  https://trello.com/c/hnFU5IQ7/516-rfp-27f-20-t...   
666                Closed  https://trello.com/c/8IRWW8vM/405-traction-pow...   
667                Closed  https://trello.com/c/12OqdIn1/34-bird-control-...   
668                Closed  https://trello.com/c/t0oBsUMh/89-cleaning-cont...   

    TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
0                     6/11/2017             nan                NaN   
1                     6/11/2017             nan                NaN   
2                      4/6/2018             nan                NaN   
3                      4/6/2018             nan                NaN   
4                     8/16/2019             nan                NaN   
..                          ...             ...                .

In [625]:
test_data

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
0                   10/11/2019      AZUNIGA  5d9e5e133c89748e6d09fe50   
1                    3/28/2019       EWELSH  5c9a22187ffbcd4fdb595644   
2                    8/30/2018       EWELSH  5b85467e8df1a105def4f6e4   
3                    3/14/2019       EWELSH  5c87e5c08d21258227d5e7e0   
4                   10/21/2018       EWELSH  5bc9db92fb62c1685a51d80e   
..                         ...          ...                       ...   
659                   6/4/2021   UNASSIGNED  60b7e349d8199b64d97ed6e7   
660                  6/11/2021   UNASSIGNED  60c0ad8a8ffd1e643ca6a001   
661                  8/18/2021   UNASSIGNED  611ad49b21c5f3226604d6c9   
662                 11/26/2021   UNASSIGNED  619e7a15d5f379538aed9640   
663                   6/8/2017   UNASSIGNED  5935fd710d0ae18f54c13cb3   

                         TRLO - Project Title TRLO - Assigned To  \
0          Trapeze Transit Master Negotiation       Arlyn Zuniga   
1    Bus Amenities Request for Qualifications         Eric Welsh   
2                        Catch Basin Cleaning         Eric Welsh   
3           Temporary Staff Program RFP (SWA)         Eric Welsh   
4              RFR 142-17 - MBTA Drug Testing         Eric Welsh   
..                                        ...                ...   
659                               Budget Tool         Unassigned   
660               Printers - Newsletter, etc.         Unassigned   
661                         Pipeline Template         Unassigned   
662                                 OCC Board         Unassigned   
663                       Buy America Auditor         Unassigned   

    TRLO - Procurement Stage TRLO - Procurement Status TRLO - Closed Project  \
0       4. FINALIZE CONTRACT                  Contract                Closed   
1       3. EVALUATE RESPONSE              Solicitation                Closed   
2                   PIPELINE                  Pipeline                Closed   
3                   PIPELINE                  Pipeline                Closed   
4        PIPELINE (Archived)                  Pipeline                Closed   
..                       ...                       ...                   ...   
659                 PIPELINE                  Pipeline                  Open   
660                 PIPELINE                  Pipeline                  Open   
661                 PIPELINE                  Pipeline                  Open   
662                 PIPELINE                  Pipeline                  Open   
663       SPECIFICATION HOLD                   On Hold                  Open   

                                    TRLO - Url (Cards)  \
0    https://trello.com/c/L2CbZXqh/518-trapeze-tran...   
1    https://trello.com/c/ezPNruB1/430-bus-amenitie...   
2    https://trello.com/c/VBWa1ACB/304-catch-basin-...   
3    https://trello.com/c/xPFn0zg3/423-temporary-st...   
4    https://trello.com/c/A3eiX1mL/343-rfr-142-17-m...   
..                                                 ...   
659      https://trello.com/c/ZjzZhn2A/749-budget-tool   
660  https://trello.com/c/LA8Eh0ra/752-printers-new...   
661  https://trello.com/c/GeKbE91l/773-pipeline-tem...   
662        https://trello.com/c/gOyRXUBA/813-occ-board   
663  https://trello.com/c/avpBel1a/4-buy-america-au...   

    TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
0                     5/18/2021             NaN                NaN   
1                     11/1/2019             NaN                NaN   
2                     9/18/2018             NaN                NaN   
3                     5/28/2019             NaN                NaN   
4                    10/19/2018             NaN                NaN   
..                          ...             ...                ...   
659                   1/12/2022             NaN                NaN   
660                   10/5/2021             NaN                NaN   
661                   

In [626]:
# Correct Due Date Dtype
trello_with_labels_right_order.loc[trello_with_labels_right_order['TRLO - Due Date'] == 'nan', 'TRLO - Due Date'] = np.nan

/Users/pbenson/opt/anaconda3/lib/python3.9/site-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/Users/pbenson/opt/anaconda3/lib/python3.9/site-packages/pandas/core/indexing.py:723: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ----------


In [627]:
def compare_projects(project_id):
    print(pd.concat([test_data.loc[test_data['TRLO - Project ID'] == project_id], trello_with_labels_right_order.loc[trello_with_labels_right_order['TRLO - Project ID'] == project_id]]).to_records())

In [628]:
compare_projects('5936005258e843c083369f7a')

[(598, '6/8/2017', 'UNASSIGNED', '5936005258e843c083369f7a', 'Printers XEROX', 'Unassigned', 'MAINTAIN CONTRACT (Archived)', 'Contract', 'Closed', 'https://trello.com/c/7Af78i02/69-printers-xerox', '6/11/2017', nan, nan, 'High Effort', nan, nan, nan, nan, nan)
 (  0, '6/5/2017', 'UNASSIGNED', '5936005258e843c083369f7a', 'Printers XEROX', 'Unassigned', 'MAINTAIN CONTRACT (Archived)', 'Contract', 'Closed', 'https://trello.com/c/7Af78i02/69-printers-xerox', '6/11/2017', nan, nan, 'High Effort', nan, nan, nan, nan, nan)]


change last updated format to %-m/%-d/%Y, change Procurement Stage, refine Procurement Status, change default due date  to nan. 

There are still ~8 rows unaccounted for. This is likely because there are no duplicate project ID's in the generated dataframe. 

In [629]:
print(trello_with_labels_right_order.columns)
print(test_data.columns)

Index(['TRLO - Project Create Date', 'TRLO - Buyer', 'TRLO - Project ID',
       'TRLO - Project Title', 'TRLO - Assigned To',
       'TRLO - Procurement Stage', 'TRLO - Procurement Status',
       'TRLO - Closed Project', 'TRLO - Url (Cards)',
       'TRLO - Last Updated (Cards)', 'TRLO - Due Date', 'TRLO - Fund Source',
       'TRLO - Level of Effort', 'TRLO - Proj In FMIS',
       'TRLO - Safety Related', 'TRLO - DEI Related', 'TRLO - SDT Review',
       'TRLO - Spend Threshold'],
      dtype='object')
Index(['TRLO - Project Create Date', 'TRLO - Buyer', 'TRLO - Project ID',
       'TRLO - Project Title', 'TRLO - Assigned To',
       'TRLO - Procurement Stage', 'TRLO - Procurement Status',
       'TRLO - Closed Project', 'TRLO - Url (Cards)',
       'TRLO - Last Updated (Cards)', 'TRLO - Due Date', 'TRLO - Fund Source',
       'TRLO - Level of Effort', 'TRLO - Proj In FMIS',
       'TRLO - Safety Related', 'TRLO - DEI Related', 'TRLO - SDT Review',
       'TRLO - Spend Threshold'],


In [581]:
columns_to_check = ['TRLO - Project Create Date', 'TRLO - Buyer', 'TRLO - Project ID',
       'TRLO - Project Title', 'TRLO - Assigned To',
       'TRLO - Procurement Stage', 'TRLO - Procurement Status',
       'TRLO - Closed Project', 'TRLO - Url (Cards)',
       'TRLO - Last Updated (Cards)', 'TRLO - Due Date', 'TRLO - Fund Source',
       'TRLO - Level of Effort', 'TRLO - Proj In FMIS',
       'TRLO - Safety Related', 'TRLO - DEI Related', 'TRLO - SDT Review',
       'TRLO - Spend Threshold']

for project_id in trello_with_labels_right_order['TRLO - Project ID'].unique():
    # Check if all columns are the same
    
    test_data_slice = test_data.loc[test_data['TRLO - Project ID'] == project_id]
    gen_data_slice = trello_with_labels_right_order.loc[trello_with_labels_right_order['TRLO - Project ID'] == project_id]
    
    for column in columns_to_check:
        test_col = list(test_data_slice[column])
        gen_col = list(gen_data_slice[column])
        if test_col != gen_col:
            if test_col[0] == test_col[0] or gen_col[0] == gen_col[0]:
                print(column, list(test_data_slice[column]), list(gen_data_slice[column]))
            #print(gen_data_slice)

TRLO - Project Create Date ['6/8/2017'] ['6/5/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/5/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/5/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/5/2017']
TRLO - Project Create Date ['6/10/2017'] ['6/8/2017']
TRLO - Project Create Date ['6/10/2017'] ['6/8/2017']
TRLO - Project Create Date ['6/10/2017'] ['6/8/2017']
TRLO - Project Create Date ['6/10/2017'] ['6/8/2017']
TRLO - Project Create Date ['1/23/2020'] ['1/21/2020']
TRLO - Project Create Date ['9/28/2019'] ['9/26/2019']
TRLO - Project Create Date ['9/27/2019'] ['9/25/2019']
TRLO - Project Create Date ['10/9/2019'] ['10/7/2019']
TRLO - Project Create Date ['10/11/2019'] ['10/9/2019']
TRLO - Project Create Date ['7/2/2020'] ['6/30/2020']
TRLO - Project Create Date ['6/8/2019'] ['6/6/2019']
TRLO - Project Create Date ['12/12/2018'] ['12/10/2018']
TRLO - Project Create Date ['2/13/2020'] ['2/11/2020']
TRLO - Project Create Date ['9/14/2019'] ['9/12/2019']
TRLO - Project Create 

IndexError: list index out of range

In [630]:
# Adjust problems here

trello_with_labels_correct = trello_with_labels_right_order.copy(deep=True)

Problems: 
- nan values aren't equal to each other. (DONE)
- Also, create dates are behind by two days. (DONE)
- There are some assigned values for names as well. (DONE)

In [631]:
right_dates = pd.to_datetime(trello_with_labels_correct['TRLO - Project Create Date']) + datetime.timedelta(days = 2)
trello_with_labels_correct['TRLO - Project Create Date'] = right_dates.dt.strftime('%-m/%-d/%Y')

In [632]:
recent_test_data = pd.read_csv('trello_4_19_output.csv')

recent_test_data.rename(columns={'TRLO -  Project ID': 'TRLO - Project ID'}, inplace=True)

In [633]:
# Recheck with correction for date
columns_to_check = ['TRLO - Project Create Date', 'TRLO - Buyer', 'TRLO - Project ID',
       'TRLO - Project Title', 'TRLO - Assigned To',
       'TRLO - Procurement Stage', 'TRLO - Procurement Status',
       'TRLO - Closed Project', 'TRLO - Url (Cards)',
       'TRLO - Last Updated (Cards)', 'TRLO - Due Date', 'TRLO - Fund Source',
       'TRLO - Level of Effort', 'TRLO - Proj In FMIS',
       'TRLO - Safety Related', 'TRLO - DEI Related', 'TRLO - SDT Review',
       'TRLO - Spend Threshold']

bad_projects = []

print('Column \t Test Date \t Calculated Data \t Project ID')
for project_id in trello_with_labels_right_order['TRLO - Project ID'].unique():
    # Check if all columns are the same
    
    test_data_slice = recent_test_data.loc[recent_test_data['TRLO - Project ID'] == project_id]
    gen_data_slice = trello_with_labels_correct.loc[trello_with_labels_correct['TRLO - Project ID'] == project_id]
    
    for column in columns_to_check:
        test_col = sorted(list(test_data_slice[column]))
        gen_col = sorted(list(gen_data_slice[column]))
        if test_col != gen_col and len(test_col) > 0:
            if test_col[0] == test_col[0] or gen_col[0] == gen_col[0]:
                print(column, list(test_data_slice[column]), list(gen_data_slice[column]))
                bad_projects.append(project_id)
            #print(gen_data_slice)

Column 	 Test Date 	 Calculated Data 	 Project ID
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['3/7/2020'] ['3/6/2020']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['2/28/2020'] ['2/27/2020']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['6/8/2017'] ['6/7/2017']
TRLO - Project Create Date ['7/24/2021'] ['7/23/2021']
TRLO - Project Create Date ['6/9/2017', '6/9/2017'] ['6/9/2017']
TRLO - Buyer ['AFLYNN', 'AFLYNN']

Problems:
- Not accounting for NEASLEY; 
- Not accounting for multiple levels of effort
- Not accounting for Potential Small Biz

In [645]:
trello_with_labels_correct['TRLO - Buyer'].unique()

array(['UNASSIGNED', 'AFLYNN', 'RWEINER', 'KHALL', 'JDELALLA', 'TDIONNE',
       'RWISE', 'EWELSH', 'JMOYNIHAN', 'MPILLEMER', 'AZUNIGA', 'no buyer'],
      dtype=object)

In [634]:
recent_test_data.loc[recent_test_data['TRLO - Project ID'] == '5937dbb9fbf481f047aa41a6']

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
111                   6/9/2017       AFLYNN  5937dbb9fbf481f047aa41a6   
112                   6/9/2017       AFLYNN  5937dbb9fbf481f047aa41a6   

    TRLO - Project Title TRLO - Assigned To TRLO - Procurement Stage  \
111           HIGH GLASS          Joe Flynn        MAINTAIN CONTRACT   
112           HIGH GLASS          Joe Flynn        MAINTAIN CONTRACT   

    TRLO - Procurement Status TRLO - Closed Project  \
111                  Contract                Closed   
112                  Contract                Closed   

                              TRLO - Url (Cards) TRLO - Last Updated (Cards)  \
111  https://trello.com/c/2b8LyJmM/80-high-glass                  12/10/2018   
112  https://trello.com/c/2b8LyJmM/80-high-glass                  12/10/2018   

    TRLO - Due Date TRLO - Fund Source TRLO - Level of Effort  \
111             NaN                NaN          Medium Effort   
112             NaN                NaN             Low Effort   

    TRLO - Proj In FMIS TRLO - Safety Related TRLO - DEI Related  \
111                 NaN                   NaN                NaN   
112                 NaN                   NaN                NaN   

    TRLO - SDT Review TRLO - Spend Threshold  
111               NaN                    NaN  
112               NaN                    NaN

In [635]:
trello_with_labels_correct.loc[trello_with_labels_correct['TRLO - Project ID'] == '5937dbb9fbf481f047aa41a6']

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
384                   6/9/2017       AFLYNN  5937dbb9fbf481f047aa41a6   

    TRLO - Project Title TRLO - Assigned To TRLO - Procurement Stage  \
384           HIGH GLASS          Joe Flynn        MAINTAIN CONTRACT   

    TRLO - Procurement Status TRLO - Closed Project  \
384                  Contract                Closed   

                              TRLO - Url (Cards) TRLO - Last Updated (Cards)  \
384  https://trello.com/c/2b8LyJmM/80-high-glass                  12/10/2018   

    TRLO - Due Date TRLO - Fund Source TRLO - Level of Effort  \
384             NaN                NaN             Low Effort   

    TRLO - Proj In FMIS TRLO - Safety Related TRLO - DEI Related  \
384                 NaN                   NaN                NaN   

    TRLO - SDT Review TRLO - Spend Threshold  
384               NaN                    NaN

In [640]:
recent_test_data.loc[recent_test_data['TRLO - Project ID'] == '5c066b71dbfa2247d5a6e768']
# different in SDT review

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
53                  12/6/2018    JMOYNIHAN  5c066b71dbfa2247d5a6e768   
54                  12/6/2018    JMOYNIHAN  5c066b71dbfa2247d5a6e768   

    TRLO - Project Title TRLO - Assigned To TRLO - Procurement Stage  \
53  FMLA Second Opinions     Jimmy Moynihan        MAINTAIN CONTRACT   
54  FMLA Second Opinions     Jimmy Moynihan        MAINTAIN CONTRACT   

   TRLO - Procurement Status TRLO - Closed Project  \
53                  Contract                  Open   
54                  Contract                  Open   

                                   TRLO - Url (Cards)  \
53  https://trello.com/c/r12848go/381-fmla-second-...   
54  https://trello.com/c/r12848go/381-fmla-second-...   

   TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
53                   1/31/2022        2/6/2019                NaN   
54                   1/31/2022        2/6/2019                NaN   

   TRLO - Level of Effort TRLO - Proj In FMIS TRLO - Safety Related  \
53             Low Effort                 NaN                   NaN   
54             Low Effort                 NaN                   NaN   

   TRLO - DEI Related                      TRLO - SDT Review  \
53                NaN  Reviewed by SDT - Potential Small Biz   
54                NaN  Reviewed by SDT - Potential Candidate   

   TRLO - Spend Threshold  
53                 <$250k  
54                 <$250k

In [642]:
trello_with_labels_correct.loc[trello_with_labels_correct['TRLO - Project ID'] == '5c066b71dbfa2247d5a6e768']
# not accounting for "reviewed by SDT - potential small biz"

TRLO - Project Create Date TRLO - Buyer         TRLO - Project ID  \
659                  12/6/2018    JMOYNIHAN  5c066b71dbfa2247d5a6e768   

     TRLO - Project Title TRLO - Assigned To TRLO - Procurement Stage  \
659  FMLA Second Opinions     Jimmy Moynihan        MAINTAIN CONTRACT   

    TRLO - Procurement Status TRLO - Closed Project  \
659                  Contract                  Open   

                                    TRLO - Url (Cards)  \
659  https://trello.com/c/r12848go/381-fmla-second-...   

    TRLO - Last Updated (Cards) TRLO - Due Date TRLO - Fund Source  \
659                   1/31/2022        2/6/2019                NaN   

    TRLO - Level of Effort TRLO - Proj In FMIS TRLO - Safety Related  \
659             Low Effort                 NaN                   NaN   

    TRLO - DEI Related                      TRLO - SDT Review  \
659                NaN  Reviewed by SDT - Potential Candidate   

    TRLO - Spend Threshold  
659                 <$250k

In [643]:
trello_with_labels_correct['TRLO - SDT Review'].unique()

array([nan, 'Reviewed by SDT - Potential Candidate',
       'Reviewed by SDT - Not a Candidate'], dtype=object)

In [646]:
print(trello_with_labels_correct['TRLO - Proj In FMIS'].unique())
print(trello_with_labels_correct['TRLO - Spend Threshold'].unique())
print(trello_with_labels_correct['TRLO - SDT Review'].unique())
print(trello_with_labels_correct['TRLO - Level of Effort'].unique())

[nan 'No Requistion Yet']
[nan '>$250k Spend' '<$250k']
[nan 'Reviewed by SDT - Potential Candidate'
 'Reviewed by SDT - Not a Candidate']
['High Effort' nan 'Medium Effort' 'Low Effort']


Label Fixes:
- Proj in FMIS
- Spend Threshold
- SDT Review

In [647]:
bad_projects

['5936005258e843c083369f7a',
 '5935ff8a24be6b67e34c664a',
 '5935fff68c18dab27b4a2433',
 '59360024def2da683e72eea7',
 '5935fd710d0ae18f54c13cb3',
 '5e6043d99c0d4e4856599082',
 '5935fd8ecaf0e2394e76301e',
 '5935fe54c12d6eabce1b3709',
 '5935fdb62b1331e331753a92',
 '5935fe7db7dec4f8df9c2cf2',
 '5935fe788616c451d1eb9447',
 '5935fdeb039444be38881dd7',
 '5e55bf47046d3b1821f5c31d',
 '5935fe92ee4d07db1dc09f95',
 '5935feba77d7f180f1a4ec79',
 '60f8b68bd9c4792dcce8d80d',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5937dbb9fbf481f047aa41a6',
 '5935fe3aee7e904ed0529610',
 '5935fe3aee7e904ed0529610',
 '5935fe1de18f8bab4d68acf2',
 '5935fdf4057cc680b8fe338b',
 '5937dbb9fbf481f047aa41b4',
 '5935fdffcf8e0fbfae1ebc64',
 '5935ff64a4726cdb17942526',
 '5935ffea95e6

In [573]:
id_board = "4d5ea62fd76aa1136000000c"
creation_time = datetime.datetime.fromtimestamp(int(id_board[0:8],16))

In [574]:
creation_time

datetime.datetime(2011, 2, 18, 12, 2, 39)